

# Creating Delaunay Lines

In this example, we show how to create AequilibraE's famous Delaunay Lines, but in Python.

For more on this topic, see its [first publication](https://xl-optim.com/delaunay/).

We use the Sioux Falls example once again.


.. seealso::
    Several functions, methods, classes and modules are used in this example:

    * :func:`aequilibrae.utils.create_delaunay_network.DelaunayAnalysis`



In [ ]:
# Imports
import pandas as pd
from uuid import uuid4
from os.path import join
import sqlite3
from tempfile import gettempdir
from geopandas import read_postgis

from aequilibrae.utils.create_example import create_example
from aequilibrae.utils.create_delaunay_network import DelaunayAnalysis

In [ ]:
# We create an empty project on an arbitrary folder
fldr = join(gettempdir(), uuid4().hex)

project = create_example(fldr)

Get the Delaunay Lines generation class



In [ ]:
da = DelaunayAnalysis(project)

# Let's create the triangulation based on the zones, but we could create based on the network (centroids) too
da.create_network("zones")

Now we get the matrix we want and create the Delaunay Lines



In [ ]:
demand = project.matrices.get_matrix("demand_omx")
demand.computational_view(["matrix"])

And we will call it 'delaunay_test'./ It will also be saved in the results_database.sqlite



In [ ]:
da.assign_matrix(demand, "delaunay_test")

we retrieve the results



In [ ]:
conn = sqlite3.connect(join(fldr, "results_database.sqlite"))
results = pd.read_sql("Select * from delaunay_test", conn).set_index("link_id")

Now we get the matrix we want and create the Delaunay Lines



In [ ]:
with project.db_connection as conn:
    links = read_postgis(
        "Select link_id, st_asBinary(geometry) geometry from delaunay_network", 
        conn, 
        geom_col="geometry", 
        crs=4326
    )
    links.set_index("link_id", inplace=True)

df = links.join(results)

max_vol = df.matrix_tot.max()

df.plot(linewidth=4 * df["matrix_tot"] / max_vol, color="blue")

Close the project



In [ ]:
project.close()